In [1]:
install_load <- function (package1, ...)  {   

   # convert arguments to vector
   packages <- c(package1, ...)

   # start loop to determine if each package is installed
   for(package in packages){

       # if package is installed locally, load
       if(package %in% rownames(installed.packages()))
          do.call('library', list(package))

       # if package is not installed locally, download, then load
       else {
          install.packages(package)
          do.call("library", list(package))
       }
   } 
}

# Section 8

Pre-load packages and MLR tasks from chapter 7, listings 7.1 - 7.8

In [18]:
install_load("mlr", "tidyverse", "mlbench", "parallel", "parallelMap", "DiagrammeR", "xgboost")

Installing package into ‘/home/nbuser/R’
(as ‘lib’ is unspecified)

Attaching package: ‘xgboost’

The following object is masked from ‘package:dplyr’:

    slice



### Listings 7.1 - 7.8 combined

In [3]:
# Listing 7.1
data(Zoo, package = "mlbench")
zooTib <- as_tibble(Zoo)

# Listing 7.2
zooTib <- mutate_if(zooTib, is.logical, as.factor)

# Listing 7.3
zooTask <- makeClassifTask(data = zooTib, target = "type")
tree <- makeLearner("classif.rpart")

# Listing 7.4
getParamSet(tree)

# Listing 7.5
treeParamSpace <- makeParamSet(
    makeIntegerParam("minsplit", lower = 5, upper = 20),
    makeIntegerParam("minbucket", lower = 3, upper = 10),
    makeNumericParam("cp", lower = 0.01, upper = 0.1),
    makeIntegerParam("maxdepth", lower = 3, upper = 10))

# Listing 7.6
randSearch <- makeTuneControlRandom(maxit = 200)
cvForTuning <- makeResampleDesc("CV", iters = 5)

# Listing 7.7
parallelStartSocket(cpus = detectCores())
tunedTreePars <- tuneParams(tree, task = zooTask,
                           resampling = cvForTuning,
                           par.set = treeParamSpace,
                           control = randSearch)
parallelStop()

# Listing 7.8
tunedTree <- setHyperPars(tree, par.vals = tunedTreePars$x)
tunedTreeModel <- train(tunedTree, zooTask)


Warning message in makeTask(type = type, data = data, weights = weights, blocking = blocking, :
“Provided data is not a pure data.frame but from class tbl_df, hence it will be converted.”

                   Type len  Def   Constr Req Tunable Trafo
minsplit        integer   -   20 1 to Inf   -    TRUE     -
minbucket       integer   -    - 1 to Inf   -    TRUE     -
cp              numeric   - 0.01   0 to 1   -    TRUE     -
maxcompete      integer   -    4 0 to Inf   -    TRUE     -
maxsurrogate    integer   -    5 0 to Inf   -    TRUE     -
usesurrogate   discrete   -    2    0,1,2   -    TRUE     -
surrogatestyle discrete   -    0      0,1   -    TRUE     -
maxdepth        integer   -   30  1 to 30   -    TRUE     -
xval            integer   -   10 0 to Inf   -   FALSE     -
parms           untyped   -    -        -   -    TRUE     -

Starting parallelization in mode=socket with cpus=2.
[Tune] Started tuning learner classif.rpart for parameter set:
             Type len Def      Constr Req Tunable Trafo
minsplit  integer   -   -     5 to 20   -    TRUE     -
minbucket integer   -   -     3 to 10   -    TRUE     -
cp        numeric   -   - 0.01 to 0.1   -    TRUE     -
maxdepth  integer   -   -     3 to 10   -    TRUE     -
With control class: TuneControlRandom
Imputation value: 1
Exporting objects to slaves for mode socket: .mlr.slave.options
Mapping in parallel: mode = socket; level = mlr.tuneParams; cpus = 2; elements = 200.
[Tune] Result: minsplit=5; minbucket=6; cp=0.0361; maxdepth=8 : mmce.test.mean=0.0790476
Stopped parallelization. All cleaned up.


## Section 8.2

In [4]:
forest <- makeLearner("classif.randomForest")

### Listing 8.1

In [5]:
forestParamSpace <- makeParamSet(
    makeIntegerParam("ntree", lower = 300, upper = 300),
    makeIntegerParam("mtry", lower = 6, upper = 12),
    makeIntegerParam("nodesize", lower = 1, upper = 5),
    makeIntegerParam("maxnodes", lower = 5, upper = 20))

randSearch <- makeTuneControlRandom(maxit = 100)

cvForTuning <- makeResampleDesc("CV", iters = 5)

parallelStartSocket(cpus = detectCores())

tunedForestPars <- tuneParams(forest, task = zooTask,
                             resampling = cvForTuning,
                             par.set = forestParamSpace,
                             control = randSearch)

parallelStop()

tunedForestPars


Starting parallelization in mode=socket with cpus=2.
[Tune] Started tuning learner classif.randomForest for parameter set:
            Type len Def     Constr Req Tunable Trafo
ntree    integer   -   - 300 to 300   -    TRUE     -
mtry     integer   -   -    6 to 12   -    TRUE     -
nodesize integer   -   -     1 to 5   -    TRUE     -
maxnodes integer   -   -    5 to 20   -    TRUE     -
With control class: TuneControlRandom
Imputation value: 1
Exporting objects to slaves for mode socket: .mlr.slave.options
Mapping in parallel: mode = socket; level = mlr.tuneParams; cpus = 2; elements = 100.
[Tune] Result: ntree=300; mtry=8; nodesize=2; maxnodes=15 : mmce.test.mean=0.0200000
Stopped parallelization. All cleaned up.


Tune result:
Op. pars: ntree=300; mtry=8; nodesize=2; maxnodes=15
mmce.test.mean=0.0200000

In [11]:
tunedForest <- setHyperPars(forest, par.vals = tunedForestPars$x)
tunedForestModel <- train(tunedForest, zooTask)

### Listing 8.2

In [15]:
forestModelData <- getLearnerModel(tunedForestModel)
species <- colnames(forestModelData$err.rate)
options(repr.plot.width=10, repr.plot.height=7)
plot(forestModelData, col = 1:length(species), lty = 1:length(species), )
legend("topright", species, col = 1:length(species), lty = 1:length(species))

### Listing 8.3

In [16]:
outer <- makeResampleDesc("CV", iters = 5)
forestWrapper <- makeTuneWrapper("classif.randomForest", 
                                resampling = cvForTuning,
                                par.set = forestParamSpace,
                                control = randSearch)

parallelStartSocket(cpus = detectCores())
cvWithTuning <- resample(forestWrapper, zooTask, resampling = outer)
parallelStop()

cvWithTuning

Starting parallelization in mode=socket with cpus=2.
Exporting objects to slaves for mode socket: .mlr.slave.options
Resampling: cross-validation
Measures:             mmce      
Mapping in parallel: mode = socket; level = mlr.resample; cpus = 2; elements = 5.


Aggregated Result: mmce.test.mean=0.0295238


Stopped parallelization. All cleaned up.


Resample Result
Task: zooTib
Learner: classif.randomForest.tuned
Aggr perf: mmce.test.mean=0.0295238
Runtime: 52.8491

## Section 8.3

In [19]:
xgb <- makeLearner("classif.xgboost")

### Listing 8.4

In [21]:
zooXgb <- mutate_at(zooTib, .vars = vars(-type), .funs = as.numeric)
xgbTask <- makeClassifTask(data = zooXgb, target = "type")

Warning message in makeTask(type = type, data = data, weights = weights, blocking = blocking, :
“Provided data is not a pure data.frame but from class tbl_df, hence it will be converted.”

### Listing 8.5

In [22]:
xgbParamSpace <- makeParamSet(
    makeNumericParam("eta", lower = 0, upper = 1),
    makeNumericParam("gamma", lower = 0, upper = 5),
    makeIntegerParam("max_depth", lower = 1, upper = 5),
    makeNumericParam("min_child_weight", lower = 1, upper = 10),
    makeNumericParam("subsample", lower = 0.5, upper = 1),
    makeNumericParam("colsample_bytree", lower = 0.5, upper = 1),
    makeIntegerParam("nrounds", lower = 20, upper = 20),
    makeDiscreteParam("eval_metric", values = c("merror", "mlogloss")))

randSearch <- makeTuneControlRandom(maxit = 1000)

cvForTuning <- makeResampleDesc("CV", iters = 5)

tunedXgbPars <- tuneParams(xgb, task = xgbTask,
                          resampling = cvForTuning,
                          par.set = xgbParamSpace,
                          control = randSearch)

tunedXgbPars

[Tune] Started tuning learner classif.xgboost for parameter set:
                     Type len Def          Constr Req Tunable Trafo
eta               numeric   -   -          0 to 1   -    TRUE     -
gamma             numeric   -   -          0 to 5   -    TRUE     -
max_depth         integer   -   -          1 to 5   -    TRUE     -
min_child_weight  numeric   -   -         1 to 10   -    TRUE     -
subsample         numeric   -   -        0.5 to 1   -    TRUE     -
colsample_bytree  numeric   -   -        0.5 to 1   -    TRUE     -
nrounds           integer   -   -        20 to 20   -    TRUE     -
eval_metric      discrete   -   - merror,mlogloss   -    TRUE     -
With control class: TuneControlRandom
Imputation value: 1
[Tune-x] 1: eta=0.883; gamma=4.66; max_depth=2; min_child_weight=7.81; subsample=0.687; colsample_bytree=0.567; nrounds=20; eval_metric=merror
[Tune-y] 1: mmce.test.mean=0.3561905; time: 0.0 min
[Tune-x] 2: eta=0.336; gamma=1.14; max_depth=4; min_child_weight=1.37;

Tune result:
Op. pars: eta=0.953; gamma=0.644; max_depth=3; min_child_weight=2.13; subsample=0.882; colsample_bytree=0.962; nrounds=20; eval_metric=merror
mmce.test.mean=0.0295238

### Listing 8.6

In [24]:
tunedXgb <- setHyperPars(xgb, par.vals = tunedXgbPars$x)
tunedXgbModel <- train(tunedXgb, xgbTask)

### Listing 8.7

In [26]:
xgbModelData <- getLearnerModel(tunedXgbModel)
ggplot(xgbModelData$evaluation_log, aes(iter, train_merror)) +
    geom_line() +
    geom_point()

### Listing 8.8

In [28]:
xgboost::xgb.plot.tree(model = xgbModelData, trees = 1:5)

HTML widgets cannot be represented in plain text (need html)

### Listing 8.9

In [30]:
outer <- makeResampleDesc("CV", iters = 3)
xgbWrapper <- makeTuneWrapper("classif.xgboost", 
                             resampling = cvForTuning,
                             par.set = xgbParamSpace,
                             control = randSearch)
cvWithTuning <- resample(xgbWrapper, xgbTask, resampling = outer)
cvWithTuning

Resampling: cross-validation
Measures:             mmce      
[Tune] Started tuning learner classif.xgboost for parameter set:
                     Type len Def          Constr Req Tunable Trafo
eta               numeric   -   -          0 to 1   -    TRUE     -
gamma             numeric   -   -          0 to 5   -    TRUE     -
max_depth         integer   -   -          1 to 5   -    TRUE     -
min_child_weight  numeric   -   -         1 to 10   -    TRUE     -
subsample         numeric   -   -        0.5 to 1   -    TRUE     -
colsample_bytree  numeric   -   -        0.5 to 1   -    TRUE     -
nrounds           integer   -   -        20 to 20   -    TRUE     -
eval_metric      discrete   -   - merror,mlogloss   -    TRUE     -
With control class: TuneControlRandom
Imputation value: 1
[Tune-x] 1: eta=0.802; gamma=1.23; max_depth=5; min_child_weight=5.42; subsample=0.555; colsample_bytree=0.639; nrounds=20; eval_metric=merror
[Tune-y] 1: mmce.test.mean=0.3505495; time: 0.0 min
[Tune-x]

Resample Result
Task: zooXgb
Learner: classif.xgboost.tuned
Aggr perf: mmce.test.mean=0.0401070
Runtime: 464.59

## Section 8.5

### Listing 8.10

In [31]:
learners = list(makeLearner("classif.knn"),
               makeLearner("classif.LiblineaRL1LogReg"),
               makeLearner("classif.svm"),
               tunedTree,
               tunedForest,
               tunedXgb)

benchCV <- makeResampleDesc("RepCV", folds = 10, reps = 5)
bench <- benchmark(learners, xgbTask, benchCV)
bench

Task: zooXgb, Learner: classif.knn
Resampling: repeated cross-validation
Measures:             mmce      
[Resample] iter 1:    0.0000000 
[Resample] iter 2:    0.0000000 
[Resample] iter 3:    0.1000000 
[Resample] iter 4:    0.0000000 
[Resample] iter 5:    0.0000000 
[Resample] iter 6:    0.0000000 
[Resample] iter 7:    0.1000000 
[Resample] iter 8:    0.0000000 
[Resample] iter 9:    0.0000000 
[Resample] iter 10:   0.0000000 
[Resample] iter 11:   0.0909091 
[Resample] iter 12:   0.0000000 
[Resample] iter 13:   0.0000000 
[Resample] iter 14:   0.0000000 
[Resample] iter 15:   0.1000000 
[Resample] iter 16:   0.0000000 
[Resample] iter 17:   0.0000000 
[Resample] iter 18:   0.0000000 
[Resample] iter 19:   0.0000000 
[Resample] iter 20:   0.1000000 
[Resample] iter 21:   0.0000000 
[Resample] iter 22:   0.0909091 
[Resample] iter 23:   0.1000000 
[Resample] iter 24:   0.0000000 
[Resample] iter 25:   0.0000000 
[Resample] iter 26:   0.0000000 
[Resample] iter 27:   0.0000000 
[Re

  task.id                learner.id mmce.test.mean
1  zooXgb               classif.knn     0.02963636
2  zooXgb classif.LiblineaRL1LogReg     0.09654545
3  zooXgb               classif.svm     0.07345455
4  zooXgb             classif.rpart     0.10672727
5  zooXgb      classif.randomForest     0.02963636
6  zooXgb           classif.xgboost     0.04745455